# VacationPy
----

#### Note
* Keep an eye on your API usage. Use https://developers.google.com/maps/reporting/gmp-reporting as reference for how to monitor your usage and billing.

* Instructions have been included for each segment. You do not have to follow them exactly, but they are included to help you think through the steps.

In [3]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import gmaps
import json
import os
from dotenv import load_dotenv
load_dotenv()
geocoder_api_key = os.getenv("geocoder_api_key")
type(geocoder_api_key)

str

### Store Part I results into DataFrame
* Load the csv exported in Part I to a DataFrame

In [4]:
city_df = pd.read_csv('clean_city_data.csv')
city_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0       tiznit   29.5833    -9.5000     79.95        19           1   
1       sokolo   14.7328    -6.1219     90.27        28          93   
2    maldonado  -34.6667   -54.9167     47.23        76           0   
3       kalabo  -14.9700    22.6814     94.37        25           5   
4      ushuaia  -54.8000   -68.3000     33.46        86          75   
..         ...       ...        ...       ...       ...         ...   
551    labuhan   -6.8844   112.2051     87.37        64          75   
552    mareeba  -17.0000   145.4333     76.48        83          62   
553       sale   34.0389    -6.8166     71.62        94         100   
554      kenai   60.5544  -151.2583     34.14        92          90   
555   tomatlan   19.9333  -105.2500     74.10        96           8   

     Wind Speed Country        Date  
0          0.51      MA  1634462485  
1          2.98      ML  1634462486  
2          4.72      UY  1634462486  
3          7.40      ZM  1634462487  
4         12.66      AR  1634462250  
..          ...     ...         ...  
551       13.91      ID  1634462734  
552        6.53      AU  1634462734  
553        0.00      MA  1634462533  
554        8.05      US  1634462735  
555        2.82      MX  1634462736  

[556 rows x 9 columns]

### Humidity Heatmap
* Configure gmaps.
* Use the Lat and Lng as locations and Humidity as the weight.
* Add Heatmap layer to map.

In [5]:
# Store latitude and longitude in locations
locations = city_df[["Latitude", "Longitude"]]
locations

Latitude  Longitude
0     29.5833    -9.5000
1     14.7328    -6.1219
2    -34.6667   -54.9167
3    -14.9700    22.6814
4    -54.8000   -68.3000
..        ...        ...
551   -6.8844   112.2051
552  -17.0000   145.4333
553   34.0389    -6.8166
554   60.5544  -151.2583
555   19.9333  -105.2500

[556 rows x 2 columns]

In [6]:
# Would fill the NaN values but we already checked it last one, ahh its all coming together, ohh and convert to float
rating = city_df["Humidity"].astype(float)

In [7]:
# Plot Heatmap
fig = gmaps.figure()

# Create heat layer
heat_layer = gmaps.heatmap_layer(locations, weights=rating,
                                    dissipating= False,
                                    max_intensity=30,
                                    point_radius=3)

# Add layer
fig.add_layer(heat_layer)

# Display figure
fig

Figure(layout=FigureLayout(height='420px'))

### Create new DataFrame fitting weather criteria
* Narrow down the cities to fit weather conditions.
* Drop any rows will null values.

In [8]:
# not a lot of conditions given on this, but lets say that nobody wants to go on vacation in places greater that 85 degrees
city_df.drop(city_df[city_df['Max Temp'] >= 85].index, inplace = True)
city_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0       tiznit   29.5833    -9.5000     79.95        19           1   
2    maldonado  -34.6667   -54.9167     47.23        76           0   
4      ushuaia  -54.8000   -68.3000     33.46        86          75   
5       touros   -5.1989   -35.4608     74.30        83          40   
6      rikitea  -23.1203  -134.9692     75.06        75           7   
..         ...       ...        ...       ...       ...         ...   
550       lata   40.1629    -8.3327     68.92        95         100   
552    mareeba  -17.0000   145.4333     76.48        83          62   
553       sale   34.0389    -6.8166     71.62        94         100   
554      kenai   60.5544  -151.2583     34.14        92          90   
555   tomatlan   19.9333  -105.2500     74.10        96           8   

     Wind Speed Country        Date  
0          0.51      MA  1634462485  
2          4.72      UY  1634462486  
4         12.66      AR  1634462250  
5         13.89      BR  1634462487  
6         14.20      PF  1634462386  
..          ...     ...         ...  
550        2.44      PT  1634462734  
552        6.53      AU  1634462734  
553        0.00      MA  1634462533  
554        8.05      US  1634462735  
555        2.82      MX  1634462736  

[493 rows x 9 columns]

In [9]:
# and while were at it nobody probably wants to go to places below freezing, if it was skiing season maybe, but its October...
# its skiing season nowhere, its only 46 locations
city_df.drop(city_df[city_df['Max Temp'] <= 32].index, inplace = True)
city_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0       tiznit   29.5833    -9.5000     79.95        19           1   
2    maldonado  -34.6667   -54.9167     47.23        76           0   
4      ushuaia  -54.8000   -68.3000     33.46        86          75   
5       touros   -5.1989   -35.4608     74.30        83          40   
6      rikitea  -23.1203  -134.9692     75.06        75           7   
..         ...       ...        ...       ...       ...         ...   
550       lata   40.1629    -8.3327     68.92        95         100   
552    mareeba  -17.0000   145.4333     76.48        83          62   
553       sale   34.0389    -6.8166     71.62        94         100   
554      kenai   60.5544  -151.2583     34.14        92          90   
555   tomatlan   19.9333  -105.2500     74.10        96           8   

     Wind Speed Country        Date  
0          0.51      MA  1634462485  
2          4.72      UY  1634462486  
4         12.66      AR  1634462250  
5         13.89      BR  1634462487  
6         14.20      PF  1634462386  
..          ...     ...         ...  
550        2.44      PT  1634462734  
552        6.53      AU  1634462734  
553        0.00      MA  1634462533  
554        8.05      US  1634462735  
555        2.82      MX  1634462736  

[447 rows x 9 columns]

In [10]:
# if its humid and cloudy then that means its likely rianing, and nobody wants to go to a place that is grey and overcast
#thats not an ideal vacation destination
#city_df.drop(city_df[["Humidity", "Cloudiness"] <= 90].index, inplace = True)
humid_df = city_df[city_df["Humidity"] <= 80]
humid_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0          tiznit   29.5833    -9.5000     79.95        19           1   
2       maldonado  -34.6667   -54.9167     47.23        76           0   
6         rikitea  -23.1203  -134.9692     75.06        75           7   
9          lompoc   34.6391  -120.4579     62.53        47           1   
15        sorland   67.6670    12.6934     37.47        72         100   
..            ...       ...        ...       ...       ...         ...   
541         lagoa   39.0500   -27.9833     68.85        78         100   
542      mananara  -16.1667    49.7667     78.26        66          44   
544   chaykovskiy   56.7686    54.1148     52.81        49          77   
546     ulladulla  -35.3500   150.4667     58.10        72          68   
547  nizhniy odes   45.3926    39.2364     68.99        52         100   

     Wind Speed Country        Date  
0          0.51      MA  1634462485  
2          4.72      UY  1634462486  
6         14.20      PF  1634462386  
9          6.91      US  1634462490  
15        18.99      NO  1634462492  
..          ...     ...         ...  
541       17.45      PT  1634462730  
542        8.77      MG  1634462730  
544       12.17      RU  1634462731  
546        6.91      AU  1634462726  
547        5.57      RU  1634462732  

[282 rows x 9 columns]

In [11]:
#nobody wants to go to place that is grey and overcast, thats not an ideal vacation destination
# theres 144 of them
hotel_df = humid_df[humid_df['Cloudiness'] <= 80]
hotel_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0         tiznit   29.5833    -9.5000     79.95        19           1   
2      maldonado  -34.6667   -54.9167     47.23        76           0   
6        rikitea  -23.1203  -134.9692     75.06        75           7   
9         lompoc   34.6391  -120.4579     62.53        47           1   
18      hermanus  -34.4187    19.2345     61.90        69          67   
..           ...       ...        ...       ...       ...         ...   
537     tongliao   43.6125   122.2653     44.71        32           4   
540     bac lieu   45.3919    19.2367     55.31        53           8   
542     mananara  -16.1667    49.7667     78.26        66          44   
544  chaykovskiy   56.7686    54.1148     52.81        49          77   
546    ulladulla  -35.3500   150.4667     58.10        72          68   

     Wind Speed Country        Date  
0          0.51      MA  1634462485  
2          4.72      UY  1634462486  
6         14.20      PF  1634462386  
9          6.91      US  1634462490  
18        11.23      ZA  1634462394  
..          ...     ...         ...  
537        6.33      CN  1634462728  
540        2.82      RS  1634462729  
542        8.77      MG  1634462730  
544       12.17      RU  1634462731  
546        6.91      AU  1634462726  

[193 rows x 9 columns]

In [12]:
hotel_df['Hotel Name'] = ""


C:\Users\mdebo\anaconda3\envs\PythonData\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [13]:
hotel_df

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0         tiznit   29.5833    -9.5000     79.95        19           1   
2      maldonado  -34.6667   -54.9167     47.23        76           0   
6        rikitea  -23.1203  -134.9692     75.06        75           7   
9         lompoc   34.6391  -120.4579     62.53        47           1   
18      hermanus  -34.4187    19.2345     61.90        69          67   
..           ...       ...        ...       ...       ...         ...   
537     tongliao   43.6125   122.2653     44.71        32           4   
540     bac lieu   45.3919    19.2367     55.31        53           8   
542     mananara  -16.1667    49.7667     78.26        66          44   
544  chaykovskiy   56.7686    54.1148     52.81        49          77   
546    ulladulla  -35.3500   150.4667     58.10        72          68   

     Wind Speed Country        Date Hotel Name  
0          0.51      MA  1634462485             
2          4.72      UY  1634462486             
6         14.20      PF  1634462386             
9          6.91      US  1634462490             
18        11.23      ZA  1634462394             
..          ...     ...         ...        ...  
537        6.33      CN  1634462728             
540        2.82      RS  1634462729             
542        8.77      MG  1634462730             
544       12.17      RU  1634462731             
546        6.91      AU  1634462726             

[193 rows x 10 columns]

### Hotel Map
* Store into variable named `hotel_df`.
* Add a "Hotel Name" column to the DataFrame.
* Set parameters to search for hotels with 5000 meters.
* Hit the Google Places API for each city's coordinates.
* Store the first Hotel result into the DataFrame.
* Plot markers on top of the heatmap.

In [15]:
# params dictionary to update each iteration
params = {
    "query": "hotel",
    "radius": 50000,
    "type": "lodging",
    "key": google_api_key
    }
base_url = "https://maps.googleapis.com/maps/api/place/textsearch/json"
    
# use the lat/lng we have to identify hotels
for index, row in hotel_df.iterrows():
    # get lat, lng from df
    lat = row["Latitude"]
    lng = row["Longitude"]
            
    # change location each iteration while leaving original params in place
    params["location"] = f"{lat},{lng}"
            
    response = requests.get(base_url, params=params)
    
    #print(f"Retrieving Results for Index {index}: {row['City']}.")
    # extract results
        
            
    # convert to json
    hotel_name = response.json()    
    #print(json.dumps(hotel_name, indent=4, sort_keys=True))
            
    # since some data may be missing we incorporate a try-except to skip any that are
    try:
        print(f"Closest hotel is {hotel_name}.")
        hotel_df.loc[index, "Hotel Name"] = hotel_name["results"][0]["name"]          
    except (KeyError, IndexError):
        print("Missing field/result.... skipping.")
            
# save data to csv
hotel_df.to_csv("Hotel_df.csv", index=False)        

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEB42-yv6xmAvUddk68Fi-vtaZRrbHA4SocEnxe3nw7naUEB554Vw2Ozz1AQXvvZPy15mkmYuo-rOuE77Xti7c40SWrTMie9RZyTpIf-LXkJ1evMyC8y1o7WNuAzuY1pBQzm-xtxE9xIZr1AmIf8ucRtvGsrYzbCXu-b7aipriMDZOdPbugDNmS2IRtrWukJemmDQ8g1Y8e0bXxPtg0sqd4hBELb4YUkGTVHv8y4ixQ_5M0CzOE21NRXm-W5BIMGVmq80Nh2PeVmJuQFmhpCfzrzVzph0z-ER1jvTmnxsMPyZCb7L_e-c93m_jbcexAH1poXbgCxJIQaoj2Ezy7Z9VAcMJAz1BYoqxGLBKTnCapEykEvWOWDif6RQnmiwd3b8Kq74lh98HhQuimDpqS3r8ST4fmw4sF6n9MRau3IDRxMX8gsn8RkmP1lYYEvoIPVdSAn8YGI', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': "4km de Tafraoute sur la Route d'Agadir via Ait Baha BP294، Tafraoute 85450, Morocco", 'geometry': {'location': {'lat': 29.7559469, 'lng': -8.9624217}, 'viewport': {'northeast': {'lat': 29.75738892989272, 'lng': -8.960963420107278}, 'southwest': {'lat': 29.75468927010727, 'lng': -8.963663079892722}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_

C:\Users\mdebo\anaconda3\envs\PythonData\lib\site-packages\pandas\core\indexing.py:1763: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEA-qbrX-kHOzNh_6U0v9L8leYDpGCpAykK6xHwOfdTiGJRv04xGCOqlnZhizh9h8jNUrcPts0Wn3_L23K0-RUManA2RL4hktCYzoKozMn1SHIIYNjWvQvpLdCSk9YfPrUET0h_AYBLqoQ92FgZ-MIDRLizP3loKeOlMWG_fsdtG9WnKoFW6CSHAHzKra-Kk9cYaPnN1FyR-Uz9Z3OJ44O6IQlCBjhv6Cv_KfbAg1NXqSK_yn89NJwpaQhXDDgIJktdTe1iamF-OALSbRFcYvkbxV4jEpA7np9sZKgY3_350u-tp_RVEPaBk9UQqhV0FVo-t1BQpMKpPZBHw4dpYRzRmdlXC63frZAW4iUHyydCmdck5BlgFfUtxWyV7RHKG_A6sv-A2zczPDIAyfYpnDczyFbHl5ABhqLPvQDa5ZxJVDeYSiuBt6e_zQhmcJ-nQZyC8vAD5', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': 'Mar Mediterraneo, 20003 Punta Ballena, Departamento de Maldonado, Uruguay', 'geometry': {'location': {'lat': -34.9085508, 'lng': -55.0447739}, 'viewport': {'northeast': {'lat': -34.90723387010728, 'lng': -55.04327962010728}, 'southwest': {'lat': -34.90993352989273, 'lng': -55.04597927989272}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color'

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEBWdOI73m4sTB3eZ10JSSjLKNvaP3RswaUPNX-N1GbLIaynObhCCETZHoRSPiIXBj2Vrjl0l403hjW-GF6SC8Td4yYq-PVqrbTvzscgWKfy9RfBe2Oy9BLq5SGa8dVMnOgK6D4lBIANr6uaPoaeraoAsdXQWy8S9JpbmtDdgi6gcr5MQdzXGJA19BiTu1JB2Nh8AuczmlrQS8WdGQ_ISYuOXVK4m4XZg13PBHFf62BNTfmKmTu75viwXuOCsCQA_WwP38hibXodY7qi2aWUCuDr0MpAajGFLcOGE3Ei1t_Tpy8YWOVsFCMR5_I308jDSyMgDLHcd1EGpUG-cNSMtoFNoBMA2ZHm5hBbyhgrVeorqTj_ixl78RLDIWFjWhDGiG2ZUtLJp-4UOVUNOGxwVTafHTi2lphEhkhk54aUFYuj6OE2EuiElQkB7ZpF0RWSEoWeeWPg', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': 'BP 19 | Archipel des Gambier, Mangareva, 98755, French Polynesia', 'geometry': {'location': {'lat': -23.1276524, 'lng': -134.9656596}, 'viewport': {'northeast': {'lat': -23.12637127010728, 'lng': -134.9643498701072}, 'southwest': {'lat': -23.12907092989272, 'lng': -134.9670495298927}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909C

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEBkaJDip48ZVBAeF8hA3NQXGh74dSd_-dD7ZTnClJz2o6xubd1ToX5E83IKrDVedlTmWOfjbbqpTQOmIUu1wyZih5XQiXn4_orHFa0tZFuOKg6lrPw36oRle3FGXNtc5YxLdhBlQPblZvyyY8j86Gt8hPGmnD0E-xSv-1K3Q1xM4xTBjk9ML2btyZdy2PQk1E3BQhUKVZ_YpaSyBD854O9zslpPPIBsIZ5eDNEb2b7cXxVZdyHVfpuEb0ccLYNoTG7zsdrWPd7BA2GOpP4bQ8PpVlXirJXrE5GifrE-MqyzmyrTkAk1TjUwwlfgBRt29SIU2aTgSG62tn3Hcvm-qxjkoqmnOx7vlUH7_oYGRRqAqSvH86XAENt0D2oH9MbIg3rt1uDnt_9CkslzYvzKIgCYkii3YWXUmotik5z5uR_McwJdzjc1qj15gqBtyVyuTxHBKRQh', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': '400 Alisal Rd, Solvang, CA 93463, United States', 'geometry': {'location': {'lat': 34.5929531, 'lng': -120.1388117}, 'viewport': {'northeast': {'lat': 34.59440262989272, 'lng': -120.1378265201073}, 'southwest': {'lat': 34.59170297010727, 'lng': -120.1405261798927}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base

...

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEAiXnxrwFOHP7x6vUd48F9j2DP1_OuzZUyhAf9bi-xgrsv1w7PNrA_nVuJ3_FtTiiCawDgd2ti3y2KX054K8gO8N4dh7g4fMZGWolcCFT75QCDEgLROKfb1O4o793cvi9Iy9cQ5KkcZJ6JHFEo8YIi0O4GKjvyyarbGRL8c4S6USZQHEueEeFG81owloRkipKLGz6ElN-CNT0GCMUV50jho9NL4T9vGgxGArT4h48SxSfvQfE_k5A5ALFMYzkl4vRY6G2dgIjDY7NSk21Ntj0Kevls_Ir4zXTy0__afg8yJlsnnFVs3uQQVNq11TG_qz6Z9_n9xmWo2m1P7dGWlpWKfS8PoYZdyuN8K4uD3mhjEY7Fyjb-ZQpqex9FpnkXYlFnchMIU4Yg5kNqI3UECEJJZqo2t8yOI0pg4vTcgt2ev39Gi-nGwIzugoZbECcM224tTLe_e', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': 'China, Inner Mongolia, Tongliao, Horqin District, Jianguo N Rd, 建国北路', 'geometry': {'location': {'lat': 43.653509, 'lng': 122.268609}, 'viewport': {'northeast': {'lat': 43.65484272989273, 'lng': 122.2697086298927}, 'southwest': {'lat': 43.65214307010729, 'lng': 122.2670089701073}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1',

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uECfnHkcsj22Agxg2FQJRSJGwvU2FywPVqbYMFT3tjFQuP4-ahpsl39dhSlSgrip-l2MlREizydVQTusdcbcK885mqAfFfKoS_iAunsaIrsPs8czGUo2GN9aZDqbawu9m8_6iMWvpYHVZm7k7VIKkYm_RCbVsVsPZDx1rsWO4tDpIggQfYNv3RY6f6Y_D8r8nrQrqhnicFA6j807zrObD3I2vTb668gjo57bket91icXqZeRCrU-QN3AO2CmVWe_B1hJdFzQFLIUhpYXTe-3kOinNdQKqGXVpqXjfptZ_atUBHtG2tPAMWFbr7wHnMk79wvgg_nAq_7Z2wku19wQIEwuH_jSgCpiIkBf-rdYKMh61d_lKQnAcAuIWqTjXVM5Ln3WmYEEXAbBn94NLlIGFJhYeCzT4POMTdJ2pNPFkUfG9Fh7hw_wV6ytX9OixMxs4eortoUt', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': 'Uspenska 1, Novi Sad 21000, Serbia', 'geometry': {'location': {'lat': 45.25450499999999, 'lng': 19.841919}, 'viewport': {'northeast': {'lat': 45.25568027989272, 'lng': 19.84327032989272}, 'southwest': {'lat': 45.25298062010728, 'lng': 19.84057067010727}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'htt

Closest hotel is {'html_attributions': [], 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': 'Masoala, Madagascar, Madagascar', 'geometry': {'location': {'lat': -15.7222279, 'lng': 49.9597273}, 'viewport': {'northeast': {'lat': -15.72087807010728, 'lng': 49.96107712989271}, 'southwest': {'lat': -15.72357772989272, 'lng': 49.95837747010727}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png', 'icon_background_color': '#909CE1', 'icon_mask_base_uri': 'https://maps.gstatic.com/mapfiles/place_api/icons/v2/hotel_pinlet', 'name': 'Masoala Forest Lodge', 'opening_hours': {'open_now': True}, 'photos': [{'height': 1282, 'html_attributions': ['<a href="https://maps.google.com/maps/contrib/103266520007669078384">A Google User</a>'], 'photo_reference': 'Aap_uEBxcV3YGImSQa51vTPxd1PN06JGfg70o-SpappCjdyPpX1qhsPnxmdnW3s9OyrvqJCxZFf6hgtN4TyuNo4PBlWzdgh6G3PwKssAaC2PVjzdiLALzCI-g0i3MBT9q2_4THUwnozHcPvI13ED-PELtFz4gYry4kyWbTt-tUm3QpfIVenT', 'width': 19

Closest hotel is {'html_attributions': [], 'next_page_token': 'Aap_uEB6pEGdH-r_za3Oj_nwEc-geYtmrux96HpCM3JbG2-IpNr_WzAoUKYVKSgfldVrwAtpu2ba6SI0gO0pkjpBt1lFNG2l3CankLxr7w88kDVQvf_fAqzLqssUKeFeKP8WERbauRGP7vgf7dRyh3OMkrnvitB22D0B3SY_NzQ0mex4oUbRtx-dcsUL651wMXR_WIOk1c1cZx1eC89bwGsCj59qvqYuFsrZWXQTMIhEUOianW-j7siNl6ilZHOl0GcoAiW1UcymS_MlkrY2PU8PcMkq4DdkRHyPFF8y0MlHHHzGP_60wQWg00LqYo0yDVhiuxdCInRhVCvxpQiNFpO0P0eIGumZ78q7QDD8HSFKX1jMeRPDaBF-HzYyeftBpMKKFTbuiA0-gRPzaLBoVoXuKHylxNzCiuOdI0DCB0szam0KRZmQtKNjPIlbRnNxslMQhYq2tvSi', 'results': [{'business_status': 'OPERATIONAL', 'formatted_address': '75 Owen St, Huskisson NSW 2540, Australia', 'geometry': {'location': {'lat': -35.038721, 'lng': 150.67236}, 'viewport': {'northeast': {'lat': -35.03749252010727, 'lng': 150.6736123798927}, 'southwest': {'lat': -35.04019217989272, 'lng': 150.6709127201073}}}, 'icon': 'https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/restaurant-71.png', 'icon_background_color': '#FF9E67', 'icon_mask_base_uri':

NameError: name 'hotels_df' is not defined

In [16]:
hotel_df.head()

City  Latitude  Longitude  Max Temp  Humidity  Cloudiness  \
0      tiznit   29.5833    -9.5000     79.95        19           1   
2   maldonado  -34.6667   -54.9167     47.23        76           0   
6     rikitea  -23.1203  -134.9692     75.06        75           7   
9      lompoc   34.6391  -120.4579     62.53        47           1   
18   hermanus  -34.4187    19.2345     61.90        69          67   

    Wind Speed Country        Date                  Hotel Name  
0         0.51      MA  1634462485  Hotel L'Arganier d'Ammelne  
2         4.72      UY  1634462486            Casapueblo Hotel  
6        14.20      PF  1634462386     Pension Bianca & Benoit  
9         6.91      US  1634462490                Hotel Corque  
18       11.23      ZA  1634462394             Houw Hoek Hotel

In [17]:
# save data to csv
hotel_df.to_csv("Hotel_df.csv", index=False)   

In [18]:
# Assign the marker layer to a variable
locations = hotel_df[["Latitude", "Longitude"]]
markers = gmaps.marker_layer(locations)

In [20]:
# NOTE: Do not change any of the code in this cell

# Using the template add the hotel marks to the heatmap
info_box_template = """
<dl>
<dt>Name</dt><dd>{Hotel Name}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
</dl>
"""
# Store the DataFrame Row
# NOTE: be sure to update with your DataFrame name
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]
locations = hotel_df[["Latitude", "Longitude"]]

In [21]:
# Create hotel symbol layer
hotel_layer = gmaps.symbol_layer(
    locations, fill_color='rgba(0, 150, 0, 0.4)',
    stroke_color='rgba(0, 0, 150, 0.4)', scale=2,
    info_box_content=hotel_info
)
# Add the layer to the map
# Display figure
fig.add_layer(markers)
fig.add_layer(hotel_layer)
fig

Figure(layout=FigureLayout(height='420px'))